# Importation des bibliothèques nécessaires

In [1]:
import pandas as pd
from pandas import ExcelWriter
import xlsxwriter
from pandas import ExcelFile
from datetime import datetime
import datetime
from datetime import timedelta
import numpy as np
import os
import statistics
from dateutil.parser import parse
import math
import calendar
from sklearn.cluster import DBSCAN
import joblib

In [2]:
# Charger le modèle à partir du fichier picklé
loaded_model = joblib.load("svm_model.pkl")

C:\Users\Lahoucine\anaconda3\Lib\site-packages\sklearn\base.py:329: UserWarning: Trying to unpickle estimator SVC from version 1.0.2 when using version 1.1.3. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(


# Création de deux fonctions utilisables dans l'importation des données

In [3]:

def toZero(x):
    try:
        converted_value = int(x)
    except ValueError:
        converted_value = 0
    return converted_value

def findDay(date):
    day, month, year = (int(i) for i in date.split('/'))
    dayNumber = calendar.weekday(year, month, day)
    return dayNumber

def arrondir_multiple_de_5(nombre):
    multiple_de_5 = round(nombre / 5) * 5
    return multiple_de_5

def process_data(df_Fusion, seuil):
    groupe = 0
    df_Fusion['Groupe'] = 0

    for index, row in df_Fusion.iterrows():
        if index == 0:
            df_Fusion.at[index, 'Groupe'] = groupe
        else:
            diff = abs(row['Talon surconso identifie'] - df_Fusion.at[index - 1, 'Talon surconso identifie'])
            if diff <= seuil:
                df_Fusion.at[index, 'Groupe'] = groupe
            else:
                groupe += 1
                df_Fusion.at[index, 'Groupe'] = groupe

    df_simplified = df_Fusion.groupby(['Groupe', 'Début surconsommation', 'Fin surconsommation']).agg({
        'Code': 'first',  # Include the 'Code' column from the original dataframe
        'Energie': 'first',  # Include the 'Energie' column from the original dataframe
        'heure ouverture': 'first',  # Include the 'heure ouverture' column from the original dataframe
        'heure fermetur': 'first',  # Include the 'heure fermetur' column from the original dataframe
        'TalonRef': 'first',  # Include the 'TalonRef' column from the original dataframe
        'Début surconsommation': 'first',
        'Fin surconsommation': 'first',
        'Talon surconso identifie': 'mean',
        'impact': 'first',  # Include the 'impact' column from the original dataframe
        'NbrHeures': 'sum',
        'NbrNuits': 'first',  # Include the 'NbrNuits' column from the original dataframe
        'Impact conso (kWh)': 'first',  # Include the 'Impact conso (kWh)' column from the original dataframe
        '% Surconso': 'first',  # Include the '% Surconso' column from the original dataframe
        "Période d'alerte": 'first',  # Include the "Période d'alerte" column from the original dataframe
        'Pourcentage de précision': 'first'  # Include the 'Pourcentage de précision' column from the original dataframe
    }).reset_index(drop=True)

    return df_simplified

# Création de l'algorithme de machine learning personnalisé que nous allons utiliser dans la fusion des heures de surconsommation.

# Cet algorithme est un algorithme de clustering non supervisé.

# Il prend en compte la successivité des heures et une marge de surconsommation.

In [4]:
import numpy as np
from sklearn.base import BaseEstimator, ClusterMixin

class TimeMarginClustering(BaseEstimator, ClusterMixin):
    def __init__(self, time_margin=1, value_margin=20):
        self.time_margin = time_margin
        self.value_margin = value_margin
        self.labels_ = None

    def fit(self, X):
        # Sort the data based on the time column (column 0)
        sorted_indices = np.argsort(X[:, 0])
        sorted_X = X[sorted_indices]

        # Initialize variables for clustering
        cluster_labels = np.zeros(len(X), dtype=int)
        current_cluster = 0
        prev_time = sorted_X[0, 0]
        prev_value = sorted_X[0, 1]

        # Iterate over the sorted data and assign cluster labels
        for i in range(len(sorted_X)):
            time = sorted_X[i, 0]
            value = sorted_X[i, 1]

            # Check if the time difference exceeds the time margin
            time_diff = time - prev_time
            if time_diff > self.time_margin:
                current_cluster += 1

            # Check if the value difference exceeds the value margin
            value_diff = abs(value - prev_value)
            if time_diff <= self.time_margin and value_diff > self.value_margin:
                current_cluster += 1

            # Assign the cluster label
            cluster_labels[i] = current_cluster

            # Update previous time and value
            prev_time = time
            prev_value = value

        # Assign the cluster labels to the algorithm's attribute
        self.labels_ = cluster_labels
        return self

    def fit_predict(self, X):
        self.fit(X)
        return self.labels_

    def predict(self, X):
        return self.fit_predict(X)

# Importation des données.

# Prétraitement des données (nettoyage des données)

# La détection de la surconsommation pour les nuits.

# L'appel et l'application de l'algorithme de fusion des heures pour les nuits.

In [5]:
writer = pd.ExcelWriter('suivi_9_sites.xlsx', engine='xlsxwriter')

Code_list=[]
TalonRef_list=[]
Date1_list=[]
Date2_list=[]
heurev_list=[]
heuref_list=[]
NbrHeure_list=[]
defrence_list=[]
surconso_identifie=[]
Energie=[]
Marge_list=[]



# Charger les données du fichier CSV
df = pd.read_csv('22.csv', sep=',', parse_dates=True, dtype={"Date":"str","Time":"str","salesforceName":"str","siteName":"str","Real Consumption (kWh)":"int64" , "TalonRef":"int64" , "Heure Ouverture":"int64" , "Heure Fermeture":"int64" , "Ouverture dim":"str" , "Margin":"int64"},converters={'Real Consumption (kWh)':toZero},encoding="utf-8-sig")
# Filtrer les données pour l'entreprise spécifiée
#print(df.columns)
for code in df["salesforceName"].unique():
    df2 = df[df["salesforceName"] == code]

    # Sélectionner les colonnes pertinentes (Date, Time, Real Consumption (kWh) , talont , ouverture , fermeture)
    df3 = df2[['Date', 'Time', 'Real Consumption (kWh)',"TalonRef" , "Heure Ouverture" , "Heure Fermeture" , "Margin"]]

    # Convertir la colonne 'Date' en type datetime avec le format approprié
    df3['Date'] = pd.to_datetime(df3['Date'], format='%Y-%m-%d')

    # Convertir la colonne 'Time' en type timedelta
    df3['Time'] = pd.to_datetime(df3['Time'], format='%H:%M:%S')

    # Combiner les colonnes 'Date' et 'Time' en une seule colonne de type datetime
    df3['DateTime'] = df3['Date'] + pd.to_timedelta(df3['Time'].dt.strftime('%H:%M:%S'))

    # Définition des heures d'ouverture et de fermeture de l'entreprise
    heure_ouverture = df3["Heure Ouverture"].iloc[0]
    heure_fermeture = df3["Heure Fermeture"].iloc[0]+1

    # Définition du talon de consommation
    talon_consommation = df3["TalonRef"].iloc[0]
    marge=df3["Margin"].iloc[0]

    # Filtrer les données pour les heures en dehors des heures d'ouverture de l'entreprise
    if heure_fermeture in [0, 1, 2]:
        donnees_filtrees = df3[(df3['DateTime'].dt.hour >= heure_fermeture) & (df3['DateTime'].dt.hour < heure_ouverture)]
    else:
        donnees_filtrees = df3[(df3['DateTime'].dt.hour >= heure_fermeture) | (df3['DateTime'].dt.hour < heure_ouverture)]


    # Calculer la différence entre la consommation réelle et le talon de consommation
    donnees_filtrees['Difference'] = donnees_filtrees['Real Consumption (kWh)'] - talon_consommation

    # Filtrer les heures de surconsommation (différence > talon_consommation * 0.08)
    heures_surconsommation = donnees_filtrees[donnees_filtrees['Difference'] > talon_consommation * 0.08]

    print("\n")
    print("\n")
    print("l'analyse de site : {}", code)
    print("\n")
    print("\n")

    # Liste des dates uniques dans votre DataFrame
    dates_uniques = heures_surconsommation['Date'].unique()

    # Parcourir chaque date et effectuer le clustering
    for i in range(len(dates_uniques) - 1):
        date_actuelle = dates_uniques[i]
        date_suivante = dates_uniques[i + 1]

        # Filtrer les données pour la date actuelle et la date suivante
        heures_nuit = heures_surconsommation[
            (heures_surconsommation['Date'] == date_actuelle) &
            (heures_surconsommation['DateTime'].dt.hour >= heure_fermeture)
        ]

        heures_nuit_suivante = heures_surconsommation[
            (heures_surconsommation['Date'] == date_suivante) &
            (heures_surconsommation['DateTime'].dt.hour < heure_ouverture)
        ]


        # Combiner les données de la nuit actuelle et de la nuit suivante
        if heure_fermeture in [0, 1, 2]:
            heures_date = heures_nuit_suivante
        else:
            heures_date = pd.concat([heures_nuit, heures_nuit_suivante])

        #print(heures_date.head(10))

        # Convertir les colonnes de surconsommation et d'impact en tableaux Numpy
        surconsommation = heures_date['DateTime'].values.reshape(-1, 1)
        # Extraire les indices et les valeurs de la colonne "Difference" des données heures_date
        indices = heures_date.index
        differences = heures_date['Difference'].values

        # Créer le tableau NumPy à partir des indices et des valeurs
        impact = np.column_stack((indices, differences))

        print(impact)
        
        if impact.size == 0:
             continue
        else:
            # Créer l'objet DBSCAN
            clustering_algo = TimeMarginClustering(time_margin=2, value_margin=marge)


            labels = clustering_algo.fit_predict(impact)

            # Ajouter les labels de clustering comme une nouvelle colonne
            heures_date['Cluster'] = labels

            # Calculer la valeur moyenne de l'impact pour chaque cluster
            clusters_moyenne = heures_date.groupby('Cluster')['Difference'].mean().reset_index()

            # Compter le nombre d'heures regroupées dans chaque cluster
            clusters_compte = heures_date.groupby('Cluster')['DateTime'].count().reset_index()
            clusters_compte = clusters_compte.rename(columns={'DateTime': 'Nombre d\'heures regroupées'})

            # Fusionner les informations de valeur moyenne et de compte dans un seul DataFrame
            clusters_info = clusters_moyenne.merge(clusters_compte, on='Cluster')

            #saver dans un excel
            for index, row in clusters_info.iterrows():
                heuref_list.append(heure_fermeture - 1)
                Code_list.append(code)
                Energie.append('Electricité')
                TalonRef_list.append(talon_consommation)
                date1 = dates_uniques[i].to_pydatetime().date()
                #date1 = datetime.datetime.strptime(date1, '%Y-%m-%d').date()
                Date1_list.append(date1)
                date2 = dates_uniques[i + 1].to_pydatetime().date()
                #date2 = datetime.datetime.strptime(date2, '%Y-%m-%d').date()
                Date2_list.append(date2)
                heurev_list.append(heure_ouverture)
                NbrHeure_list.append(row['Nombre d\'heures regroupées'])
                defrence_list.append(int(row['Difference']))
                surconso_identifie.append(talon_consommation+int(row['Difference']))
                Marge_list.append(marge)

            # Afficher les informations des clusters pour la date spécifique
            print("\n")
            print(f"Date: {dates_uniques[i]}")
            print("\n")
            print(clusters_info)
            print("\n")
          

df_NuitOut = pd.DataFrame({'Code':Code_list, 'Energie': Energie,'heure ouverture':heurev_list,'heure fermetur':heuref_list, 'TalonRef':TalonRef_list, 'Début surconsommation':Date1_list, 'Fin surconsommation':Date2_list, 'Talon surconso identifie':surconso_identifie, 'impact':defrence_list,'NbrHeures':NbrHeure_list, 'Marge':Marge_list})

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3731806557.py:18: ParserWarning: Both a converter and dtype were specified for column Real Consumption (kWh) - only the converter will be used.
  df = pd.read_csv('22.csv', sep=',', parse_dates=True, dtype={"Date":"str","Time":"str","salesforceName":"str","siteName":"str","Real Consumption (kWh)":"int64" , "TalonRef":"int64" , "Heure Ouverture":"int64" , "Heure Fermeture":"int64" , "Ouverture dim":"str" , "Margin":"int64"},converters={'Real Consumption (kWh)':toZero},encoding="utf-8-sig")
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3731806557.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%Y-%m-%d')
C:\Users\Lahoucine\AppData\Lo





l'analyse de site : {} CS467








l'analyse de site : {} CS531




[[  117    23]
 [  118    19]
 [  119    14]
 [58317    23]
 [58318    19]
 [58319    14]
 [  120    15]
 [  121    16]
 [  122    17]
 [  123    20]]


Date: 2024-02-01 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0   18.142857                           7
1        1   17.666667                           3


[[141  22]
 [142  22]
 [143  14]
 [144  15]
 [145  14]
 [146  16]
 [147  15]]


Date: 2024-02-02 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0        22.0                           2
1        1        14.8                           5


[[165  20]
 [166  17]
 [167  16]
 [168  14]
 [169  15]
 [170  16]
 [171  16]]


Date: 2024-02-03 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0   16.285714                           7


[[  189    19]
 [  190    17]
 [  191    14]
 [58200    16]
 [58201    15]
 [58202    18]
 [58203    17]]


Date: 2

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3731806557.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%Y-%m-%d')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3731806557.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Time'] = pd.to_datetime(df3['Time'], format='%H:%M:%S')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3731806557.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a D



Date: 2024-02-02 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0        51.5                           2
1        1       103.0                           1


[[58825    29]
 [58826    18]
 [58827    70]]


Date: 2024-02-03 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0        23.5                           2
1        1        70.0                           1


[[58849    28]
 [58850    18]
 [58851    67]]


Date: 2024-01-29 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0        23.0                           2
1        1        67.0                           1


[[58873    26]
 [58874    17]
 [58875    66]]


Date: 2024-01-30 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0        21.5                           2
1        1        66.0                           1






l'analyse de site : {} MO2147




[[  693    18]
 [  694    20]
 [  695    20]
 [59037    18]
 [59038    20]
 [59039  

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3731806557.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%Y-%m-%d')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3731806557.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Time'] = pd.to_datetime(df3['Time'], format='%H:%M:%S')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3731806557.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a D

...

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3731806557.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%Y-%m-%d')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3731806557.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Time'] = pd.to_datetime(df3['Time'], format='%H:%M:%S')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3731806557.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a D





l'analyse de site : {} CS123




[[ 57335      8]
 [128279      8]
 [ 57337      5]
 [ 57338      7]]


Date: 2024-02-01 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         7.0                           3
1        1         7.0                           1


[[57359     5]]


Date: 2024-02-02 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         5.0                           1






l'analyse de site : {} MP3412








l'analyse de site : {} MP3404




[[ 57527      2]
 [128519      2]
 [ 57530      2]]


Date: 2024-02-01 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         2.0                           1
1        1         2.0                           1
2        2         2.0                           1


[[57551     2]
 [57554     2]]


Date: 2024-02-02 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         2.0                           1
1        1         2.0          

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3731806557.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%Y-%m-%d')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3731806557.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Time'] = pd.to_datetime(df3['Time'], format='%H:%M:%S')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3731806557.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a D



Date: 2024-02-03 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         6.0                           1
1        1        25.0                           1


[[128763      6]
 [128764     27]]


Date: 2024-02-04 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         6.0                           1
1        1        27.0                           1


[[128787      9]
 [128788     27]]


Date: 2024-01-28 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         9.0                           1
1        1        27.0                           1


[[128811      8]
 [128812     28]]


Date: 2024-01-29 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         8.0                           1
1        1        28.0                           1


[[128834      6]
 [128835      8]
 [128836     28]]


Date: 2024-01-30 00:00:00


   Cluster  Difference  Nombre d'heures regroupées
0        0         7.0

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3731806557.py:28: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%Y-%m-%d')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3731806557.py:31: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Time'] = pd.to_datetime(df3['Time'], format='%H:%M:%S')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3731806557.py:34: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a D

# La détection de la surconsommation pour les dimanches.

# L'appel et l'application de l'algorithme de fusion des heures pour les dimanches.

# L'organisation des sorties dans une feuille d'un fichier Excel.

In [6]:
dCode_list=[]
dTalonRef_list=[]
dDate1_list=[]
dDate2_list=[]
dheurev_list=[]
dheuref_list=[]
dNbrHeure_list=[]
ddefrence_list=[]
dsurconso_identifie=[]
dEnergie=[]
dNbrNuit=[]
Impact_conso = []
perSurconso = []
Periode = []


# Convert 'Date' column to datetime type if needed
df['Date'] = pd.to_datetime(df['Date'])

# Filter the data to keep only Sundays
sundays_data = df[df['Date'].dt.weekday == 6]

# Print the filtered data
#print(sundays_data.head(30))
df = sundays_data
for code in df["salesforceName"].unique():
    df2 = df[df["salesforceName"] == code]

    # Select relevant columns: Date, Time, Real Consumption (kWh), TalonRef, Heure Ouverture, Heure Fermeture, Ouverture dim
    df3 = df2[['Date', 'Time', 'Real Consumption (kWh)', 'TalonRef', 'Heure Ouverture', 'Heure Fermeture', 'Ouverture dim' , 'Margin']]

    # Convert the 'Date' column to datetime type with the appropriate format
    df3['Date'] = pd.to_datetime(df3['Date'], format='%d/%m/%Y')

    # Convert the 'Time' column to timedelta type
    df3['Time'] = pd.to_timedelta(df3['Time'])

    # Combine the 'Date' and 'Time' columns into a single datetime column
    df3['DateTime'] = df3['Date'] + df3['Time']

    # Define the opening and closing hours of the company
    heure_ouverture = df3["Heure Ouverture"].iloc[0]
    heure_fermeture = df3["Heure Fermeture"].iloc[0] + 1
    ouverture_dim = df3["Ouverture dim"].iloc[0]

    # Define the consumption threshold
    talon_consommation = df3["TalonRef"].iloc[0]
    marge=df3["Margin"].iloc[0]

    # Filter the data for hours outside the company's opening hours
    if ouverture_dim == "Journée":
        donnees_filtrees = pd.DataFrame()
    elif ouverture_dim == "Fermé":
        donnees_filtrees = df3[(df3['DateTime'].dt.hour >= heure_ouverture) & (df3['DateTime'].dt.hour < heure_fermeture)]
    elif ouverture_dim == "Matin":
        donnees_filtrees = df3[(df3['DateTime'].dt.hour >= 14) & (df3['DateTime'].dt.hour < heure_fermeture)]

    if len(donnees_filtrees) > 0:
        # Calculate the difference between the actual consumption and the consumption threshold
        donnees_filtrees['Difference'] = donnees_filtrees['Real Consumption (kWh)'] - talon_consommation

        # Filter the overconsumption hours (difference > talon_consommation * 0.08)
        heures_surconsommation = donnees_filtrees[donnees_filtrees['Difference'] > talon_consommation * 0.08]

        # Print the hours of overconsumption
        if len(heures_surconsommation) > 0:
            print(heures_surconsommation)

        print("\n")
        print("\n")
        print("l'analyse de site : {}", code)
        print("\n")
        print("\n")

        print(len(heures_surconsommation))

        # Liste des dates uniques dans votre DataFrame
        dates_uniques = heures_surconsommation['Date'].unique()
        
        # Parcourir chaque date et effectuer le clustering
        for i in range(len(dates_uniques)-1):
            date = dates_uniques[i+1]

            heures_date = heures_surconsommation[(heures_surconsommation['Date'] == date)]
            #print(heures_date.head(10))

            # Convertir les colonnes de surconsommation et d'impact en tableaux Numpy
            surconsommation = heures_date['DateTime'].values.reshape(-1, 1)
            # Extraire les indices et les valeurs de la colonne "Difference" des données heures_date
            indices = heures_date.index
            differences = heures_date['Difference'].values

            # Créer le tableau NumPy à partir des indices et des valeurs
            impact = np.column_stack((indices, differences))

            
            # Créer l'objet DBSCAN
            clustering_algo = TimeMarginClustering(time_margin=2, value_margin=marge)

            labels = clustering_algo.fit_predict(impact)

            # Ajouter les labels de clustering comme une nouvelle colonne
            heures_date['Cluster'] = labels

            # Calculer la valeur moyenne de l'impact pour chaque cluster
            clusters_moyenne = heures_date.groupby('Cluster')['Difference'].mean().reset_index()

            # Compter le nombre d'heures regroupées dans chaque cluster
            clusters_compte = heures_date.groupby('Cluster')['DateTime'].count().reset_index()
            clusters_compte = clusters_compte.rename(columns={'DateTime': 'Nombre d\'heures regroupées'})

            # Fusionner les informations de valeur moyenne et de compte dans un seul DataFrame
            clusters_info = clusters_moyenne.merge(clusters_compte, on='Cluster')

            #saver dans un excel
            for index, row in clusters_info.iterrows():
                dheuref_list.append(heure_fermeture - 1)
                dCode_list.append(code)
                dEnergie.append('Electricité')
                dTalonRef_list.append(talon_consommation)
                date1 = dates_uniques[i+1].to_pydatetime().date()
                dDate1_list.append(date1)
               # date_string = np.datetime_as_string(dates_uniques[i+1], unit='D')
                #date2 = datetime.datetime.strptime(date_string, '%Y-%m-%d').date()
                dDate2_list.append(date1)
                dheurev_list.append(heure_ouverture)
                dNbrHeure_list.append(row['Nombre d\'heures regroupées'])
                ddefrence_list.append(int(row['Difference']))
                dsurconso_identifie.append(arrondir_multiple_de_5(talon_consommation+int(row['Difference'])))
                surconso = row['Nombre d\'heures regroupées'] * int(row['Difference'])
                dNbrNuit.append(1)
                Impact_conso.append(surconso)

                persurconso = (int(row['Difference']) /  talon_consommation)*100
                persurconso = int(persurconso)
                persurconso = str(persurconso)
                persurconso = persurconso + '%'
                perSurconso.append(persurconso)
                Periode.append('Dim')

df_dimOut = pd.DataFrame({'Code':dCode_list, 'Energie': dEnergie,'heure ouverture':dheurev_list,'heure fermetur':dheuref_list, 'TalonRef':dTalonRef_list, 'Début surconsommation':dDate1_list, 'Fin surconsommation':dDate2_list, 'Talon surconso identifie':dsurconso_identifie, 'impact':ddefrence_list,'NbrHeures':dNbrHeure_list, 'NbrNuits':dNbrNuit, 'Impact conso (kWh)':Impact_conso, '% Surconso':perSurconso, "Période d'alerte":Periode})
grouped_df = df_dimOut.groupby("Code").size().reset_index(name="Nombre de lignes")
grouped_df["Pourcentage de précision"] = 100 - (grouped_df["Nombre de lignes"] - 1) * 10
df = df_dimOut.merge(grouped_df[["Code", "Pourcentage de précision"]], on="Code", how="left")
df['Pourcentage de précision'] = df['Pourcentage de précision'].astype(str) + '%'
df = process_data(df , 5)

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\1839643628.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%d/%m/%Y')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\1839643628.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Time'] = pd.to_timedelta(df3['Time'])
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\1839643628.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usin

            Date            Time  Real Consumption (kWh)  TalonRef  \
172   2024-02-04 0 days 04:00:00                      62        45   
173   2024-02-04 0 days 05:00:00                      67        45   
174   2024-02-04 0 days 06:00:00                      68        45   
175   2024-02-04 0 days 07:00:00                      66        45   
176   2024-02-04 0 days 08:00:00                      66        45   
177   2024-02-04 0 days 09:00:00                      64        45   
178   2024-02-04 0 days 10:00:00                      62        45   
179   2024-02-04 0 days 11:00:00                      62        45   
180   2024-02-04 0 days 12:00:00                      63        45   
181   2024-02-04 0 days 13:00:00                      61        45   
182   2024-02-04 0 days 14:00:00                      63        45   
183   2024-02-04 0 days 15:00:00                      63        45   
184   2024-02-04 0 days 16:00:00                      62        45   
185   2024-02-04 0 d

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\1839643628.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Time'] = pd.to_timedelta(df3['Time'])
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\1839643628.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['DateTime'] = df3['Date'] + df3['Time']
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\1839643628.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexe

            Date            Time  Real Consumption (kWh)  TalonRef  \
60494 2024-01-28 0 days 14:00:00                      33        25   
60495 2024-01-28 0 days 15:00:00                      34        25   
60496 2024-01-28 0 days 16:00:00                      33        25   
60497 2024-01-28 0 days 17:00:00                      35        25   
60498 2024-01-28 0 days 18:00:00                      35        25   
60499 2024-01-28 0 days 19:00:00                      34        25   
60500 2024-01-28 0 days 20:00:00                      28        25   

       Heure Ouverture  Heure Fermeture Ouverture dim  Margin  \
60494                5               20         Matin      10   
60495                5               20         Matin      10   
60496                5               20         Matin      10   
60497                5               20         Matin      10   
60498                5               20         Matin      10   
60499                5               20         M

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\1839643628.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%d/%m/%Y')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\1839643628.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Time'] = pd.to_timedelta(df3['Time'])
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\1839643628.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usin

...

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\1839643628.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%d/%m/%Y')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\1839643628.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Time'] = pd.to_timedelta(df3['Time'])
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\1839643628.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usin

             Date            Time  Real Consumption (kWh)  TalonRef  \
55478  2024-02-04 0 days 14:00:00                      57        50   
55479  2024-02-04 0 days 15:00:00                      57        50   
55480  2024-02-04 0 days 16:00:00                      57        50   
55482  2024-02-04 0 days 18:00:00                      55        50   
125774 2024-01-28 0 days 14:00:00                      62        50   
125775 2024-01-28 0 days 15:00:00                      60        50   
125776 2024-01-28 0 days 16:00:00                      61        50   
125777 2024-01-28 0 days 17:00:00                      60        50   
125778 2024-01-28 0 days 18:00:00                      60        50   
125779 2024-01-28 0 days 19:00:00                      60        50   
125780 2024-01-28 0 days 20:00:00                      60        50   

        Heure Ouverture  Heure Fermeture Ouverture dim  Margin  \
55478                 4               20         Matin      10   
55479          

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\1839643628.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%d/%m/%Y')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\1839643628.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Time'] = pd.to_timedelta(df3['Time'])
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\1839643628.py:39: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try usin

             Date            Time  Real Consumption (kWh)  TalonRef  \
57974  2024-02-04 0 days 14:00:00                      21        10   
57975  2024-02-04 0 days 15:00:00                      21        10   
57976  2024-02-04 0 days 16:00:00                      23        10   
57977  2024-02-04 0 days 17:00:00                      22        10   
57978  2024-02-04 0 days 18:00:00                      21        10   
57979  2024-02-04 0 days 19:00:00                      20        10   
57980  2024-02-04 0 days 20:00:00                      16        10   
57981  2024-02-04 0 days 21:00:00                      15        10   
128894 2024-01-28 0 days 14:00:00                      23        10   
128895 2024-01-28 0 days 15:00:00                      22        10   
128896 2024-01-28 0 days 16:00:00                      25        10   
128897 2024-01-28 0 days 17:00:00                      23        10   
128898 2024-01-28 0 days 18:00:00                      23        10   
128899

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\1839643628.py:103: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  heures_date['Cluster'] = labels
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\1839643628.py:33: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df3['Date'] = pd.to_datetime(df3['Date'], format='%d/%m/%Y')
C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\1839643628.py:36: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row

# Prétraitement des données et appel du modèle de machine learning (Random Forest) pour dimanches.

In [7]:
data = df[["Talon surconso identifie", "impact", "NbrHeures", "NbrNuits", "Impact conso (kWh)", "% Surconso", "Période d'alerte"]]
data.head()

Talon surconso identifie  impact  NbrHeures  NbrNuits  Impact conso (kWh)  \
0                      65.0      19       17.0         1               228.0   
1                     110.0      42        6.0         1               252.0   
2                     100.0      30        4.0         1               120.0   
3                     107.5      48        8.0         1               336.0   
4                      50.0      19        7.0         1               133.0   

  % Surconso Période d'alerte  
0        42%              Dim  
1        60%              Dim  
2        42%              Dim  
3        80%              Dim  
4        63%              Dim

In [8]:
print(data.dtypes)

Talon surconso identifie    float64
impact                        int64
NbrHeures                   float64
NbrNuits                      int64
Impact conso (kWh)          float64
% Surconso                   object
Période d'alerte             object
dtype: object


In [9]:
# Transformation de la colonne '% Surconso' en float
data['% Surconso'] = data['% Surconso'].apply(lambda x: float(x.strip('%')) / 100)

# Affichage du dataframe après la transformation
data.head()

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3833681290.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['% Surconso'] = data['% Surconso'].apply(lambda x: float(x.strip('%')) / 100)


Talon surconso identifie  impact  NbrHeures  NbrNuits  Impact conso (kWh)  \
0                      65.0      19       17.0         1               228.0   
1                     110.0      42        6.0         1               252.0   
2                     100.0      30        4.0         1               120.0   
3                     107.5      48        8.0         1               336.0   
4                      50.0      19        7.0         1               133.0   

   % Surconso Période d'alerte  
0        0.42              Dim  
1        0.60              Dim  
2        0.42              Dim  
3        0.80              Dim  
4        0.63              Dim

In [10]:
# Créer un dictionnaire de mapping
mapping = {"Nuit": 0, "Dim": 1, "Jour": 2, "Jour/nuit": 3, "Jour/Nuit": 3}

# Remplacer les valeurs de la colonne 'Catégorie' par les entiers correspondants
data["Période d'alerte"] = data["Période d'alerte"].replace(mapping)

# Afficher les 5 premières lignes du DataFrame
data.head()

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3671493290.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data["Période d'alerte"] = data["Période d'alerte"].replace(mapping)


Talon surconso identifie  impact  NbrHeures  NbrNuits  Impact conso (kWh)  \
0                      65.0      19       17.0         1               228.0   
1                     110.0      42        6.0         1               252.0   
2                     100.0      30        4.0         1               120.0   
3                     107.5      48        8.0         1               336.0   
4                      50.0      19        7.0         1               133.0   

   % Surconso  Période d'alerte  
0        0.42                 1  
1        0.60                 1  
2        0.42                 1  
3        0.80                 1  
4        0.63                 1

In [11]:
# Faire des prédictions pour chaque ligne de la dataframe
predictions = loaded_model.predict(data)
df["Catégorie"] = predictions
# Créer un dictionnaire de mapping
mapping = {0: "Investigation en cours", 1: "Changement de comportement", 2: "Eclairage", 3: "Froid", 4: "CVC", 5:"Multi-usage"}

# Remplacer les valeurs de la colonne 'Catégorie' par les entiers correspondants
df['Catégorie'] = df['Catégorie'].replace(mapping)
df.head(15)

C:\Users\Lahoucine\anaconda3\Lib\site-packages\sklearn\base.py:493: FutureWarning: The feature names should match those that were passed during fit. Starting version 1.2, an error will be raised.
Feature names unseen at fit time:
- NbrHeures
- NbrNuits
- Talon surconso identifie
- impact
Feature names seen at fit time, yet now missing:
- DP Surconso (kW)
- Nb d'heures
- Nb nuits/jours concernés
- Talon surconso identifié

  warnings.warn(message, FutureWarning)


Code      Energie  heure ouverture  heure fermetur  TalonRef  \
0    CS531  Electricité                4              20        45   
1   MO0160  Electricité                5              23        70   
2   MO0160  Electricité                5              23        70   
3   MO1244  Electricité                5              21        60   
4   MO2147  Electricité                5              20        30   
5    CS271  Electricité                4              22        45   
6    CS271  Electricité                4              22        45   
7    CS271  Electricité                4              22        45   
8    CS271  Electricité                4              22        45   
9    CS271  Electricité                4              22        45   
10   CS271  Electricité                4              22        45   
11   CS271  Electricité                4              22        45   
12   CS271  Electricité                4              22        45   
13   CS990  Electricité                4              21        45   
14   CS990  Electricité                4              21        45   

   Début surconsommation Fin surconsommation  Talon surconso identifie  \
0             2024-01-28          2024-01-28                 65.000000   
1             2024-01-28          2024-01-28                110.000000   
2             2024-01-28          2024-01-28                100.000000   
3             2024-01-28          2024-01-28                107.500000   
4             2024-01-28          2024-01-28                 50.000000   
5             2024-01-28          2024-01-28                 72.500000   
6             2024-01-28          2024-01-28                130.000000   
7             2024-01-28          2024-01-28                100.000000   
8             2024-01-28          2024-01-28                 76.666667   
9             2024-01-28          2024-01-28                 95.000000   
10            2024-01-28          2024-01-28                105.000000   
11            2024-01-28          2024-01-28                 95.000000   
12            2024-01-28          2024-01-28                 70.000000   
13            2024-01-28          2024-01-28                 50.000000   
14            2024-01-28          2024-01-28                 75.000000   

    impact  NbrHeures  NbrNuits  Impact conso (kWh) % Surconso  \
0       19       17.0         1               228.0        42%   
1       42        6.0         1               252.0        60%   
2       30        4.0         1               120.0        42%   
3       48        8.0         1               336.0        80%   
4       19        7.0         1               133.0        63%   
5       23        3.0         1                46.0        51%   
6       84        1.0         1                84.0       186%   
7       56        4.0         1               224.0       124%   
8       30        5.0         1                90.0        66%   
9       48        1.0         1                48.0       106%   
10      59        1.0         1                59.0       131%   
11      50        1.0         1                50.0       111%   
12      23        3.0         1                69.0        51%   
13       4        1.0         1                 4.0         8%   
14      32        1.0         1                32.0        71%   

   Période d'alerte Pourcentage de précision                   Catégorie  
0               Dim                      80%  Changement de comportement  
1               Dim                      90%  Changement de comportement  
2               Dim                      90%  Changement de comportement  
3               Dim                      90%  Changement de comportement  
4               Dim                     100%                         CVC  
5               Dim                       0%                         CVC  
6               Dim                       0%  Changement de comportement  
7               Dim                       0

In [12]:
df.to_excel(writer, sheet_name='dim', index=False)

# Création de l'algorithme de machine learning personnalisé que nous allons utiliser dans la fusion des nuits de surconsommation.

# Il prend en compte la successivité des dates, une marge de surconsommation et une marge des heures.

In [13]:
def custom_clustering(X, date_margin, consumption_margin, hours_margin, cond):
    clusters = []
    remaining_points = X.copy()

    while len(remaining_points) > 0:
        current_point = remaining_points[0]
        cluster = [current_point]
        remaining_points = np.delete(remaining_points, 0, axis=0)
        i = 0

        # Sauvegarde de la valeur originale de date_margin
        original_date_margin = date_margin

        while i < len(remaining_points):
            point = remaining_points[i]


            if (abs(point[0] - current_point[0]) <= date_margin and
                abs(point[1] - current_point[1]) <= consumption_margin and
                abs(point[2] - current_point[2]) <= hours_margin):

                current_point = point
                cluster.append(point)
                remaining_points = np.delete(remaining_points, i, axis=0)
            else:
                i += 1

            # Vérification de la condition et mise à jour de date_margin si nécessaire
            if point[2] >= cond:
                date_margin = 1

        # Rétablissement de la valeur originale de date_margin
        date_margin = original_date_margin

        clusters.append(cluster)

    return clusters
def create_cluster_dataframe(clusters):
    cluster_data=[]
    for cluster in clusters:
        consomption_mean = np.mean([point[1] for point in cluster])
        hours_mean = np.mean([point[2] for point in cluster])
        count = len(cluster)
        cluster_data.append([consomption_mean ,hours_mean , count])
    df = pd.DataFrame(cluster_data, columns=['Mean Consomption' , 'Mean Hours', 'Count'])
    return df

# L'appel et l'application de l'algorithme de fusion des nuits sur les données output de fusion des heures pour les nuits.

In [14]:
Code_list=[]
TalonRef_list=[]
Date1_list=[]
Date2_list=[]
heurev_list=[]
heuref_list=[]
NbrHeure_list=[]
defrence_list=[]
surconso_identifie=[]
Energie=[]
NbrNuit_list=[]
NImpact_conso = []
NperSurconso = []
NPeriode = []



for code in df_NuitOut["Code"].unique():
    df_Nuit = df_NuitOut[df_NuitOut["Code"] == code]
    # Votre code précédent ici...

    # Créer un tableau Numpy à partir des colonnes spécifiées
    X = np.column_stack((df_Nuit.index, df_Nuit['Talon surconso identifie'], df_Nuit['NbrHeures']))

    print(X)
    cond = (23 - df_Nuit['heure fermetur'].iloc[0])+df_Nuit['heure ouverture'].iloc[0]
    marge=df_Nuit['Marge'].iloc[0]
   
    clusters = custom_clustering(X , date_margin=2 , consumption_margin=marge , hours_margin=2 , cond=cond)
    
    df = create_cluster_dataframe(clusters)
    print(df.head(5))

    for (index, row), cluster in zip(df.iterrows(), clusters):
        Energie.append('Electricité')
        heuref_list.append(df_Nuit['heure fermetur'].iloc[0])
        Code_list.append(code)
        TalonRef_list.append(df_Nuit['TalonRef'].iloc[0])
        first_index = int(cluster[0][0])
        Date1_list.append(df_NuitOut['Début surconsommation'].iloc[first_index])
        last_index = int(cluster[-1][0])
        Date2_list.append(df_NuitOut['Fin surconsommation'].iloc[last_index])
        heurev_list.append(df_Nuit['heure ouverture'].iloc[0])
        surconso_identifie.append(arrondir_multiple_de_5(int(row['Mean Consomption'])))
        defrence_list.append(int(row['Mean Consomption']) - df_Nuit['TalonRef'].iloc[0])
        NbrHeure_list.append(round(row['Mean Hours']))
        NbrNuit_list.append(row['Count'])
        surconso = round(row['Mean Hours']) * (int(row['Mean Consomption']) - df_Nuit['TalonRef'].iloc[0]) * row['Count']
        NImpact_conso.append(surconso)

        persurconso = ((int(row['Mean Consomption']) - df_Nuit['TalonRef'].iloc[0]) /  df_Nuit['TalonRef'].iloc[0])*100
        persurconso = int(persurconso)
        persurconso = str(persurconso)
        persurconso = persurconso + '%'
        NperSurconso.append(persurconso)
        NPeriode.append('Nuit')

df_Fusion = pd.DataFrame({'Code':Code_list, 'Energie': Energie,'heure ouverture':heurev_list,'heure fermetur':heuref_list, 'TalonRef':TalonRef_list, 'Début surconsommation':Date1_list, 'Fin surconsommation':Date2_list, 'Talon surconso identifie':surconso_identifie, 'impact':defrence_list,'NbrHeures':NbrHeure_list, 'NbrNuits':NbrNuit_list, 'Impact conso (kWh)':NImpact_conso, '% Surconso':NperSurconso, "Période d'alerte":NPeriode})
grouped_df = df_Fusion.groupby("Code").size().reset_index(name="Nombre de lignes")
grouped_df["Pourcentage de précision"] = np.maximum(30, 100 - (grouped_df["Nombre de lignes"] - 1) * 10)
df = df_Fusion.merge(grouped_df[["Code", "Pourcentage de précision"]], on="Code", how="left")
df['Pourcentage de précision'] = df['Pourcentage de précision'].astype(str) + '%'
df = process_data(df , 5)

[[ 0. 63.  7.]
 [ 1. 62.  3.]
 [ 2. 67.  2.]
 [ 3. 59.  5.]
 [ 4. 61.  7.]
 [ 5. 61.  3.]
 [ 6. 61.  4.]
 [ 7. 70.  1.]
 [ 8. 61.  6.]
 [ 9. 66.  2.]
 [10. 60.  5.]
 [11. 61.  7.]]
   Mean Consomption  Mean Hours  Count
0              63.0         7.0      1
1              64.5         2.5      2
2              60.0         6.0      2
3              60.8         5.0      5
4              68.0         1.5      2
[[ 12.  84.   5.]
 [ 13.  82.   5.]
 [ 14.  80.   5.]
 [ 15. 103.   5.]
 [ 16. 101.   5.]
 [ 17.  87.   5.]
 [ 18.  85.   5.]]
   Mean Consomption  Mean Hours  Count
0              82.0         5.0      3
1             102.0         5.0      2
2              86.0         5.0      2
[[ 19.  74.   1.]
 [ 20.  74.   1.]
 [ 21.  76.   1.]
 [ 22.  78.   1.]
 [ 23. 102.   2.]
 [ 24.  76.   1.]]
   Mean Consomption  Mean Hours  Count
0              75.6         1.0      5
1             102.0         2.0      1
[[25. 79.  7.]
 [26. 75.  2.]
 [27. 74.  7.]
 [28. 68.  7.]
 [29. 89.  1.]
 

   Mean Consomption  Mean Hours  Count
0         39.800000         1.0      5
1         40.333333         1.0      6
2         40.000000         6.0      1
[[350. 100.   7.]
 [351.  98.   3.]
 [352. 102.   7.]
 [353. 100.   7.]
 [354.  98.   3.]
 [355.  92.   4.]
 [356.  98.   7.]
 [357. 100.   7.]
 [358.  96.   7.]]
   Mean Consomption  Mean Hours  Count
0        100.666667         7.0      3
1         98.000000         3.0      1
2         95.000000         3.5      2
3         98.000000         7.0      3
[[359. 240.   5.]
 [360. 238.   1.]
 [361. 234.   5.]
 [362. 227.   5.]
 [363. 234.   1.]
 [364. 226.   4.]
 [365. 232.   5.]
 [366. 235.   5.]
 [367. 237.   5.]]
   Mean Consomption  Mean Hours  Count
0        233.666667        5.00      3
1        238.000000        1.00      1
2        234.000000        1.00      1
3        232.500000        4.75      4
[[368. 399.   2.]
 [369. 420.   1.]
 [370. 437.   2.]
 [371. 435.   1.]
 [372. 396.   1.]
 [373. 446.   2.]
 [374. 423.   2.]
 [

[[815.  50.   2.]
 [816.  49.   1.]
 [817.  58.   1.]
 [818.  49.   1.]
 [819.  50.   1.]
 [820.  50.   1.]
 [821.  50.   3.]
 [822.  52.   1.]
 [823.  50.   2.]]
   Mean Consomption  Mean Hours  Count
0              50.0         1.5      8
1              58.0         1.0      1
[[824.  44.   1.]
 [825.  44.   3.]
 [826.  83.   1.]
 [827.  61.   4.]
 [828.  44.   3.]
 [829.  44.   2.]]
   Mean Consomption  Mean Hours  Count
0              44.0         2.0      2
1              83.0         1.0      1
2              61.0         4.0      1
3              44.0         2.5      2
[[830.  51.   7.]
 [831.  51.   3.]
 [832.  52.   7.]
 [833.  50.   3.]
 [834.  52.   4.]
 [835.  50.   3.]
 [836.  58.   4.]
 [837.  53.   7.]
 [838.  53.   4.]
 [839.  51.   3.]
 [840.  52.   7.]]
   Mean Consomption  Mean Hours  Count
0             51.50        7.00      2
1             50.75        3.25      4
2             58.00        4.00      1
3             53.00        7.00      1
4             52.00   

   Mean Consomption  Mean Hours  Count
0              49.0    6.000000      1
1              51.0    2.571429      7
[[1.299e+03 5.000e+01 1.000e+00]
 [1.300e+03 5.000e+01 1.000e+00]]
   Mean Consomption  Mean Hours  Count
0              50.0         1.0      2
[[1.301e+03 1.750e+02 3.000e+00]
 [1.302e+03 1.790e+02 3.000e+00]
 [1.303e+03 1.520e+02 3.000e+00]
 [1.304e+03 1.560e+02 3.000e+00]
 [1.305e+03 1.520e+02 2.000e+00]
 [1.306e+03 1.660e+02 1.000e+00]
 [1.307e+03 1.530e+02 3.000e+00]
 [1.308e+03 1.550e+02 2.000e+00]
 [1.309e+03 1.690e+02 1.000e+00]]
   Mean Consomption  Mean Hours  Count
0             177.0         3.0      2
1             153.6         2.6      5
2             166.0         1.0      1
3             169.0         1.0      1
[[1.310e+03 7.100e+01 1.000e+00]
 [1.311e+03 7.200e+01 1.000e+00]
 [1.312e+03 7.100e+01 1.000e+00]
 [1.313e+03 6.900e+01 1.000e+00]
 [1.314e+03 7.100e+01 1.000e+00]
 [1.315e+03 7.000e+01 1.000e+00]
 [1.316e+03 6.800e+01 1.000e+00]]
   Mean Conso

   Mean Consomption  Mean Hours  Count
0              79.0         1.0      1
[[1.912e+03 5.000e+01 1.000e+00]
 [1.913e+03 5.000e+01 1.000e+00]
 [1.914e+03 5.100e+01 1.000e+00]
 [1.915e+03 4.900e+01 1.000e+00]
 [1.916e+03 5.100e+01 1.000e+00]
 [1.917e+03 5.000e+01 1.000e+00]]
   Mean Consomption  Mean Hours  Count
0         50.166667         1.0      6
[[1.918e+03 1.000e+02 1.000e+00]
 [1.919e+03 1.020e+02 1.000e+00]
 [1.920e+03 9.900e+01 1.000e+00]
 [1.921e+03 1.020e+02 1.000e+00]
 [1.922e+03 1.010e+02 1.000e+00]]
   Mean Consomption  Mean Hours  Count
0             100.8         1.0      5
[[1.923e+03 8.900e+01 3.000e+00]
 [1.924e+03 9.000e+01 1.000e+00]
 [1.925e+03 9.000e+01 1.000e+00]
 [1.926e+03 8.700e+01 1.000e+00]
 [1.927e+03 9.000e+01 1.000e+00]
 [1.928e+03 8.700e+01 1.000e+00]
 [1.929e+03 8.700e+01 1.000e+00]]
   Mean Consomption  Mean Hours  Count
0         88.571429    1.285714      7
[[1.930e+03 7.500e+01 6.000e+00]
 [1.931e+03 7.600e+01 1.000e+00]
 [1.932e+03 1.040e+02 2.0

   Mean Consomption  Mean Hours  Count
0        153.000000         5.0      1
1        155.000000         1.0      1
2        215.000000         1.0      1
3        123.000000         4.0      1
4        135.666667         1.0      3
[[2.398e+03 5.000e+01 7.000e+00]
 [2.399e+03 5.000e+01 2.000e+00]
 [2.400e+03 5.100e+01 7.000e+00]
 [2.401e+03 5.000e+01 7.000e+00]
 [2.402e+03 5.000e+01 2.000e+00]
 [2.403e+03 2.800e+01 1.000e+00]
 [2.404e+03 2.200e+01 1.000e+00]]
   Mean Consomption  Mean Hours  Count
0         50.333333         7.0      3
1         50.000000         2.0      1
2         50.000000         2.0      1
3         25.000000         1.0      2
[[2.405e+03 1.000e+02 2.000e+00]
 [2.406e+03 9.800e+01 1.000e+00]
 [2.407e+03 1.030e+02 1.000e+00]
 [2.408e+03 1.230e+02 7.000e+00]
 [2.409e+03 1.240e+02 7.000e+00]
 [2.410e+03 1.230e+02 2.000e+00]
 [2.411e+03 1.210e+02 1.000e+00]
 [2.412e+03 1.290e+02 2.000e+00]
 [2.413e+03 1.000e+02 1.000e+00]
 [2.414e+03 1.270e+02 3.000e+00]
 [2.415e+

   Mean Consomption  Mean Hours  Count
0         44.666667    7.000000      3
1         52.000000    2.000000      1
2         40.000000    2.000000      1
3         43.333333    6.333333      3
4         48.000000    1.000000      2
[[2.996e+03 2.940e+02 5.000e+00]
 [2.997e+03 2.980e+02 1.000e+00]
 [2.998e+03 3.180e+02 2.000e+00]
 [2.999e+03 2.930e+02 5.000e+00]
 [3.000e+03 3.370e+02 1.000e+00]
 [3.001e+03 2.960e+02 5.000e+00]
 [3.002e+03 3.450e+02 1.000e+00]
 [3.003e+03 2.920e+02 2.000e+00]
 [3.004e+03 2.950e+02 3.000e+00]
 [3.005e+03 3.380e+02 1.000e+00]
 [3.006e+03 2.940e+02 5.000e+00]
 [3.007e+03 3.460e+02 1.000e+00]
 [3.008e+03 3.010e+02 5.000e+00]
 [3.009e+03 3.550e+02 1.000e+00]
 [3.010e+03 3.000e+02 5.000e+00]
 [3.011e+03 3.440e+02 1.000e+00]]
   Mean Consomption  Mean Hours  Count
0            294.00        5.00      1
1            324.50        1.25      4
2            294.50        5.00      2
3            296.40        4.00      5
4            345.75        1.00      4
[[3

   Mean Consomption  Mean Hours  Count
0              58.0        7.00      1
1              64.0        1.25      4
2              59.0        4.00      1
3              58.0        2.50      2
4              58.5        6.50      2
[[3.498e+03 7.200e+01 1.000e+00]
 [3.499e+03 7.900e+01 4.000e+00]
 [3.500e+03 7.700e+01 1.000e+00]
 [3.501e+03 7.700e+01 1.000e+00]
 [3.502e+03 6.800e+01 1.000e+00]
 [3.503e+03 5.700e+01 1.000e+00]
 [3.504e+03 5.600e+01 6.000e+00]
 [3.505e+03 5.400e+01 6.000e+00]
 [3.506e+03 5.400e+01 6.000e+00]]
   Mean Consomption  Mean Hours  Count
0         75.333333         1.0      3
1         79.000000         4.0      1
2         68.000000         1.0      1
3         57.000000         1.0      1
4         54.666667         6.0      3
[[3.507e+03 1.700e+01 4.000e+00]
 [3.508e+03 1.700e+01 2.000e+00]
 [3.509e+03 1.800e+01 4.000e+00]]
   Mean Consomption  Mean Hours  Count
0         17.333333    3.333333      3
[[3.510e+03 1.470e+02 1.000e+00]
 [3.511e+03 1.860e+02 6

   Mean Consomption  Mean Hours  Count
0           221.875         1.5      8
1           268.000         1.0      1
[[3.979e+03 3.900e+01 2.000e+00]
 [3.980e+03 2.300e+01 1.000e+00]
 [3.981e+03 3.900e+01 2.000e+00]
 [3.982e+03 2.300e+01 1.000e+00]
 [3.983e+03 3.900e+01 2.000e+00]
 [3.984e+03 2.400e+01 1.000e+00]
 [3.985e+03 3.900e+01 2.000e+00]
 [3.986e+03 2.200e+01 2.000e+00]
 [3.987e+03 3.900e+01 2.000e+00]
 [3.988e+03 2.300e+01 1.000e+00]
 [3.989e+03 3.900e+01 2.000e+00]]
   Mean Consomption  Mean Hours  Count
0              39.0         2.0      6
1              23.0         1.2      5
[[3.990e+03 3.400e+01 7.000e+00]
 [3.991e+03 4.000e+01 2.000e+00]
 [3.992e+03 3.000e+01 4.000e+00]
 [3.993e+03 3.600e+01 1.000e+00]
 [3.994e+03 3.300e+01 7.000e+00]]
   Mean Consomption  Mean Hours  Count
0              34.0         7.0      1
1              38.0         1.5      2
2              30.0         4.0      1
3              33.0         7.0      1
[[3.995e+03 5.500e+01 1.000e+00]
 [3.996e

# Prétraitement des données et appel du modèle de machine learning (Random Forest) pour nuits.

In [15]:
data = df[["Talon surconso identifie", "impact", "NbrHeures", "NbrNuits", "Impact conso (kWh)", "% Surconso", "Période d'alerte"]]
data.head()

Talon surconso identifie  impact  NbrHeures  NbrNuits  Impact conso (kWh)  \
0                      65.0      18          7       1.0               126.0   
1                      65.0      19          2       2.0                76.0   
2                      60.0      15          6       2.0               180.0   
3                      60.0      15          5       5.0               375.0   
4                      70.0      23          2       2.0                92.0   

  % Surconso Période d'alerte  
0        40%             Nuit  
1        42%             Nuit  
2        33%             Nuit  
3        33%             Nuit  
4        51%             Nuit

In [16]:
print(data.dtypes)

Talon surconso identifie    float64
impact                        int64
NbrHeures                     int64
NbrNuits                    float64
Impact conso (kWh)          float64
% Surconso                   object
Période d'alerte             object
dtype: object


In [17]:
# Transformation de la colonne '% Surconso' en float
data['% Surconso'] = data['% Surconso'].apply(lambda x: float(x.strip('%')) / 100)

# Affichage du dataframe après la transformation
data.head()

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3833681290.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['% Surconso'] = data['% Surconso'].apply(lambda x: float(x.strip('%')) / 100)


Talon surconso identifie  impact  NbrHeures  NbrNuits  Impact conso (kWh)  \
0                      65.0      18          7       1.0               126.0   
1                      65.0      19          2       2.0                76.0   
2                      60.0      15          6       2.0               180.0   
3                      60.0      15          5       5.0               375.0   
4                      70.0      23          2       2.0                92.0   

   % Surconso Période d'alerte  
0        0.40             Nuit  
1        0.42             Nuit  
2        0.33             Nuit  
3        0.33             Nuit  
4        0.51             Nuit

In [18]:
# Créer un dictionnaire de mapping
mapping = {"Nuit": 0, "Dim": 1, "Jour": 2, "Jour/nuit": 3, "Jour/Nuit": 3}

# Remplacer les valeurs de la colonne 'Catégorie' par les entiers correspondants
data["Période d'alerte"] = data["Période d'alerte"].replace(mapping)

# Afficher les 20 premières lignes du DataFrame
data.head()

C:\Users\Lahoucine\AppData\Local\Temp\ipykernel_10652\3054528154.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data["Période d'alerte"] = data["Période d'alerte"].replace(mapping)


Talon surconso identifie  impact  NbrHeures  NbrNuits  Impact conso (kWh)  \
0                      65.0      18          7       1.0               126.0   
1                      65.0      19          2       2.0                76.0   
2                      60.0      15          6       2.0               180.0   
3                      60.0      15          5       5.0               375.0   
4                      70.0      23          2       2.0                92.0   

   % Surconso  Période d'alerte  
0        0.40                 0  
1        0.42                 0  
2        0.33                 0  
3        0.33                 0  
4        0.51                 0

In [19]:
# Faire des prédictions pour chaque ligne de la dataframe
predictions = loaded_model.predict(data)
df["Catégorie"] = predictions
# Créer un dictionnaire de mapping
mapping = {0: "Investigation en cours", 1: "Changement de comportement", 2: "Eclairage", 3: "Froid", 4: "CVC", 5:"Multi-usage"}

# Remplacer les valeurs de la colonne 'Catégorie' par les entiers correspondants
df['Catégorie'] = df['Catégorie'].replace(mapping)
df.head(15)

C:\Users\Lahoucine\anaconda3\Lib\site-packages\sklearn\base.py:493: FutureWarning: The feature names should match those that were passed during fit. Starting version 1.2, an error will be raised.
Feature names unseen at fit time:
- NbrHeures
- NbrNuits
- Talon surconso identifie
- impact
Feature names seen at fit time, yet now missing:
- DP Surconso (kW)
- Nb d'heures
- Nb nuits/jours concernés
- Talon surconso identifié

  warnings.warn(message, FutureWarning)


Code      Energie  heure ouverture  heure fermetur  TalonRef  \
0    CS531  Electricité                4              20        45   
1    CS531  Electricité                4              20        45   
2    CS531  Electricité                4              20        45   
3    CS531  Electricité                4              20        45   
4    CS531  Electricité                4              20        45   
5   MO0160  Electricité                5              23        70   
6   MO0160  Electricité                5              23        70   
7   MO0160  Electricité                5              23        70   
8   MO0102  Electricité                5              21        65   
9   MO0102  Electricité                5              21        65   
10  MO1244  Electricité                5              21        60   
11  MO1244  Electricité                5              21        60   
12  MO1244  Electricité                5              21        60   
13  MO1244  Electricité                5              21        60   
14  MO1244  Electricité                5              21        60   

   Début surconsommation Fin surconsommation  Talon surconso identifie  \
0             2024-02-01          2024-02-02                      65.0   
1             2024-02-01          2024-02-03                      65.0   
2             2024-02-02          2024-02-04                      60.0   
3             2024-02-04          2024-01-31                      60.0   
4             2024-01-28          2024-01-30                      70.0   
5             2024-02-01          2024-02-04                      80.0   
6             2024-02-04          2024-01-29                     100.0   
7             2024-01-29          2024-01-31                      85.0   
8             2024-02-01          2024-01-30                      75.0   
9             2024-02-04          2024-01-29                     100.0   
10            2024-02-01          2024-02-02                      75.0   
11            2024-02-01          2024-02-03                      75.0   
12            2024-02-03          2024-02-04                      70.0   
13            2024-02-04          2024-01-28                      87.5   
14            2024-02-04          2024-01-28                      65.0   

    impact  NbrHeures  NbrNuits  Impact conso (kWh) % Surconso  \
0       18          7       1.0               126.0        40%   
1       19          2       2.0                76.0        42%   
2       15          6       2.0               180.0        33%   
3       15          5       5.0               375.0        33%   
4       23          2       2.0                92.0        51%   
5       12          5       3.0               180.0        17%   
6       32          5       2.0               320.0        45%   
7       16          5       2.0               160.0        22%   
8       10          1       5.0                50.0        15%   
9       37          2       1.0                74.0        56%   
10      15          2       1.0                30.0        25%   
11      16          7       2.0               224.0        26%   
12       8          7       1.0                56.0        13%   
13      29          2       1.0                29.0        48%   
14       5          1       2.0                10.0         8%   

   Période d'alerte Pourcentage de précision                   Catégorie  
0              Nuit                      60%                         CVC  
1              Nuit                      60%                         CVC  
2              Nuit                      60%                         CVC  
3              Nuit                      60%  Changement de comportement  
4              Nuit                      60%                         CVC  
5              Nuit                      80%                         CVC  
6              Nuit                      80%  Changement de comportement  
7              Nuit                      80

In [20]:
df.to_excel(writer, sheet_name='Nuit', index=False)
print('---------------------------Sauvegarde---------------------------')
#writer.save()
writer.close()
print('---------------------------Fin analyse détection auto---------------------------')

---------------------------Sauvegarde---------------------------
---------------------------Fin analyse détection auto---------------------------


In [21]:
#import pandas as pd

#df_ref = pd.read_excel('fichier2.xlsx', sheet_name='Conso P60', header=0, skiprows=0)
#df_ref.to_csv('data.csv', index=False, encoding='utf-8-sig')